# Biblioteca de Algoritmos - Lab 03

Nos últimos anos, muitas bibliotecas RL foram desenvolvidas. Essas bibliotecas foram projetadas para ter todas as ferramentas necessárias para implementar e testar agentes de Aprendizado por Reforço .

Ainda assim, elas se diferem muito. É por isso que é importante escolher uma biblioteca que seja rápida, confiável e relevante para sua tarefa de RL. Do ponto de vista técnico, existem algumas coisas a se ter em mente ao considerar uma bilioteca para RL.

- **Suporte para bibliotecas de aprendizado de máquina existentes:** Como o RL normalmente usa algoritmos baseados em gradiente para aprender e ajustar funções de política, você vai querer que ele suporte sua biblioteca favorita (Tensorflow, Keras, Pytorch, etc.)
- **Escalabilidade:** RL é computacionalmente intensivo e ter a opção de executar de forma distribuída torna-se importante ao atacar ambientes complexos.
- **Composibilidade:** Os algoritmos de RL normalmente envolvem simulações e muitos outros componentes. Você vai querer uma biblioteca que permita reutilizar componentes de algoritmos de RL, que seja compatível com várias estruturas de aprendizado profundo.

[Aqui](https://docs.google.com/spreadsheets/d/1ZWhViAwCpRqupA5E_xFHSaBaaBZ1wAjO6PvmmEEpXGI/edit#gid=0) você consegue visualizar uma lista com algumas bibliotecas existentes.

<img src="https://i1.wp.com/neptune.ai/wp-content/uploads/RL-tools.png?resize=1024%2C372&ssl=1" width=500>


## Ray RLlib

[Ray](https://docs.ray.io/en/latest/) é uma plataforma de execução distribuída que fornece bases para paralelismo e escalabilidade que são simples de usar e permitem que os programas Python sejam escalados em qualquer lugar, de um notebook a um grande cluster. Além disso, construída sobre o Ray, temos a [RLlib](https://docs.ray.io/en/latest/rllib.html), que fornece uma API unificada que pode ser aproveitada em uma ampla gama de aplicações.

<br>

<img src="https://miro.medium.com/max/1838/1*_bomm09XtiZfQ52Kfz9Ciw.png" width=600>


A RLlib foi projetada para oferecer suporte a várias estruturas de aprendizado profundo (TensorFlow e PyTorch) e pode ser acessada por meio de uma API Python simples. Atualmente, ela vem com uma [série de algoritmos RL](https://docs.ray.io/en/latest/rllib-algorithms.html#available-algorithms-overview).

Em particular, a RLlib permite um desenvolvimento rápido porque torna mais fácil construir algoritmos RL escaláveis ​​por meio da reutilização e montagem de implementações existentes. A RLlib também permite que os desenvolvedores usem redes neurais criadas com várias estruturas de aprendizado profundo e se integra facilmente a simuladores de terceiros.


## (Iniciar Colab) Configuração

Você precisará fazer uma cópia deste notebook em seu Google Drive antes de editar. Você pode fazer isso com **Arquivo → Salvar uma cópia no Drive**.

In [ ]:
import os
from google.colab import drive
drive.mount("/content/gdrive")
isColab = True

In [ ]:
# Seu trabalho será armazenado em uma pasta chamada `minicurso_rl` por padrão 
# para evitar que o tempo limite da instância do Colab exclua suas edições

DRIVE_PATH = "/content/gdrive/MyDrive/minicurso_rl/lab03"
DRIVE_PYTHON_PATH = DRIVE_PATH.replace("\\", "")
if not os.path.exists(DRIVE_PYTHON_PATH):
  %mkdir -p $DRIVE_PATH

In [ ]:
! wget http://www.atarimania.com/roms/Roms.rar
! mkdir /content/ROM/
! unrar e /content/Roms.rar /content/ROM/ -y
! python -m atari_py.import_roms /content/ROM/ > /dev/null 2>&1

## (Iniciar somente local, fora do COLAB) Configuração

In [3]:
import os
isColab = False

In [4]:
import copy

# Seu trabalho será armazenado em uma pasta chamada `minicurso_rl` por padrão 
# para evitar que o tempo limite da instância do Colab exclua suas edições
CONTENT_PATH = "./content"
if not os.path.exists(CONTENT_PATH):
    %mkdir $CONTENT_PATH

CKPT_PATH = "./ckpt"
if not os.path.exists(CKPT_PATH):
    %mkdir $CKPT_PATH

if not isColab:
    DRIVE_PATH = copy.deepcopy(CONTENT_PATH)

In [5]:
# ! wget http://www.atarimania.com/roms/Roms.rar
# ! mkdir ./content/ROM/
# ! mv ./Roms.rar ./content/
# ! unrar e ./content/Roms.rar ./content/ROM/ -y
# ! python -m atari_py.import_roms ./content/ROM/ > /dev/null 2>&1

## (Sempre) Outras configurações

In [ ]:
# Ambiente da competição
!pip install --upgrade ceia-soccer-twos > /dev/null 2>&1
# a versão do ray compatível com a implementação dos agentes disponibilizada é a 1.4.0
!pip install 'aioredis==1.3.1' > /dev/null 2>&1 
!pip install 'aiohttp==3.7.4' > /dev/null 2>&1 
!pip install 'ray==1.4.0' > /dev/null 2>&1 
!pip install 'ray[rllib]==1.4.0' > /dev/null 2>&1 
!pip install 'ray[tune]==1.4.0' > /dev/null 2>&1 
!pip install torch > /dev/null 2>&1 
!pip install lz4 > /dev/null 2>&1
!pip install gym[atari] > /dev/null 2>&1
!pip install GPUtil /dev/null 2>&1

# Dependências necessárias para gravar os vídeos
!apt-get install -y xvfb x11-utils > /dev/null 2>&1 
!pip install pyvirtualdisplay==0.2.* > /dev/null 2>&1

In [7]:
# Inicializa uma instância de um display virtual
from pyvirtualdisplay import Display
display = Display(visible=False, size=(1400, 900))
_ = display.start()

INFO:pyvirtualdisplay.abstractdisplay:Successfully started X with display ":1009".


In [8]:
# Carrega a extensão do notebook TensorBoard
%load_ext tensorboard

In [9]:
def get_checkpoint_path(mode='best', env='soccer', algorithm='ppo', version='1.0'):
    if isColab:
        path = '/content/minicurso_rl/lab02/ckpt/'
    else:
        path = './ckpt/'

    return path + env + '_' + mode + '_' + algorithm + '_' + version + '_ckpt.pth'

## (Sempre) Ambiente

O OpenAI Gym possui um wrapper VideoRecorder que pode gravar um vídeo do ambiente em formato MP4. Abaixo iremos interagir no ambiente do [Carpole](https://gym.openai.com/envs/CartPole-v0/) executando ações aleatórias e gravar o resultado.

In [10]:
import gym
from gym.wrappers.monitoring.video_recorder import VideoRecorder

environment_id = "CartPole-v0"

In [11]:
import gym
from gym.wrappers.monitoring.video_recorder import VideoRecorder

env = gym.make(environment_id)
before_training = os.path.join(
    DRIVE_PATH, "{}_before_training.mp4".format(environment_id)
)
print(before_training)

video = VideoRecorder(env, before_training)
env.reset()
done = False
while not done:
    env.render()
    video.capture_frame()
    observation, reward, done, info = env.step(env.action_space.sample())

video.close()
env.close()

./content/CartPole-v0_before_training.mp4


O código acima salvou o arquivo de vídeo no seu Drive. Para exibi-lo no notebook, você precisa de uma função auxiliar.

In [12]:
from base64 import b64encode
def render_mp4(videopath: str) -> str:
    mp4 = open(videopath, 'rb').read()
    base64_encoded_mp4 = b64encode(mp4).decode()
    return f'<video width=400 controls><source src="data:video/mp4;' \
         f'base64,{base64_encoded_mp4}" type="video/mp4"></video>'

O código abaixo renderiza os resultados. Você deve obter um vídeo semelhante ao abaixo.

In [ ]:
from IPython.display import HTML
html = render_mp4(before_training)
HTML(html)

## Treinando um agente de Aprendizado por Reforço

Primeiro, vamos começar a executar o Ray em segundo plano. Executar um `ray.shutdown()` seguido por um `ray.init()` deve dar início às coisas.

In [11]:
import ray

ray.shutdown()
ray.init(ignore_reinit_error=True, include_dashboard=False)

{'node_ip_address': '192.168.0.102',
 'raylet_ip_address': '192.168.0.102',
 'redis_address': '192.168.0.102:6379',
 'object_store_address': '/tmp/ray/session_2021-11-16_17-41-22_051049_6159/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-11-16_17-41-22_051049_6159/sockets/raylet',
 'webui_url': None,
 'session_dir': '/tmp/ray/session_2021-11-16_17-41-22_051049_6159',
 'metrics_export_port': 60883,
 'node_id': 'de7325ee89abb038669f710e177bba49ad8ea92740b57643b532c0a9'}

### Basic Python API

Em alto nível, RLlib fornece uma classe Trainer que contém uma política para interação com o ambiente. Por meio da interface do Trainer, a política pode ser treinada, avaliada ou computar uma ação. 

Para cada algoritmo gostaríamos de configurar os parâmetros (taxa de aprendizado, tamanho da rede, tamanho do batch, etc.) de acordo com a nossa aplicação.  Para isso o Ray fornece dois níveis de paramêtros que podemos alterar. Primeiramente temos os parâmetros comuns a todos os algoritmos. Você pode conferir uma lista com os parâmetros disponíveis através desse [link](https://docs.ray.io/en/latest/rllib-training.html#common-parameters).

E para cada [algoritmo disponível no ray](https://docs.ray.io/en/latest/rllib-algorithms.html#available-algorithms-overview) temos os parâmetros específicos. Na imagem abaixo podemos ver os parâmetros específicos para o algoritmo [Policy Gradient](https://docs.ray.io/en/latest/rllib-algorithms.html#policy-gradients).


<img src='https://drive.google.com/uc?id=1yKJDJViHE_F9JH7NTQMYtQL3KLBJoJyk' width="500" >


In [12]:
import ray
import ray.rllib.agents.pg as pg
from ray.tune.logger import pretty_print

config = pg.DEFAULT_CONFIG.copy()
config["num_gpus"] = 0
config["num_workers"] = 1
config["lr"] = 0.0004
config["framework"] = "torch"

trainer = pg.PGTrainer(config=config, env=environment_id)
episodes = 1000

for i in range(episodes):
   # Executa uma iteração de treinamento da política com Policy Gradient (PG)
    result = trainer.train()
    print(pretty_print(result))

    if i % 100 == 0:
        checkpoint = trainer.save()
        print("checkpoint saved at", checkpoint)

last_checkpoint = trainer.save()

2021-11-16 17:41:58,945	INFO trainer.py:696 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.


agent_timesteps_total: 200
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-42-06
done: false
episode_len_mean: 19.7
episode_media: {}
episode_reward_max: 41.0
episode_reward_mean: 19.7
episode_reward_min: 11.0
episodes_this_iter: 10
episodes_total: 10
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 7.660465240478516
  num_agent_steps_sampled: 200
  num_steps_sampled: 200
  num_steps_trained: 200
iterations_since_restore: 1
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 19.4
  gpu_util_percent0: 0.08
  ram_util_percent: 51.4
  vram_util_percent0: 0.07584731819677526
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.049669351150740434
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.07061341508704036
  mean_inference_ms: 1.2711434815060438
  mean_r

agent_timesteps_total: 1600
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-42-08
done: false
episode_len_mean: 23.514705882352942
episode_media: {}
episode_reward_max: 68.0
episode_reward_mean: 23.514705882352942
episode_reward_min: 9.0
episodes_this_iter: 9
episodes_total: 68
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 7.896124839782715
  num_agent_steps_sampled: 1600
  num_steps_sampled: 1600
  num_steps_trained: 1600
iterations_since_restore: 8
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 36.7
  gpu_util_percent0: 0.02
  ram_util_percent: 51.4
  vram_util_percent0: 0.07370845672918723
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04499006021706943
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.06582676441750579
  mean_inference_ms

agent_timesteps_total: 3000
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-42-09
done: false
episode_len_mean: 28.91
episode_media: {}
episode_reward_max: 81.0
episode_reward_mean: 28.91
episode_reward_min: 9.0
episodes_this_iter: 5
episodes_total: 105
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 11.492469787597656
  num_agent_steps_sampled: 3000
  num_steps_sampled: 3000
  num_steps_trained: 3000
iterations_since_restore: 15
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 31.8
  gpu_util_percent0: 0.06
  ram_util_percent: 45.9
  vram_util_percent0: 0.05478775913129319
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.044048139170800374
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.064993412914786
  mean_inference_ms: 0.906225779704747
  me

agent_timesteps_total: 4400
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-42-11
done: false
episode_len_mean: 37.58
episode_media: {}
episode_reward_max: 130.0
episode_reward_mean: 37.58
episode_reward_min: 11.0
episodes_this_iter: 3
episodes_total: 131
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 14.83127212524414
  num_agent_steps_sampled: 4400
  num_steps_sampled: 4400
  num_steps_trained: 4400
iterations_since_restore: 22
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 31.1
  gpu_util_percent0: 0.07
  ram_util_percent: 44.6
  vram_util_percent0: 0.05577492596248766
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04310529312963243
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.06407645308126694
  mean_inference_ms: 0.8506834197011175
 

...

agent_timesteps_total: 193400
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-17
done: false
episode_len_mean: 199.3
episode_media: {}
episode_reward_max: 200.0
episode_reward_mean: 199.3
episode_reward_min: 176.0
episodes_this_iter: 1
episodes_total: 1176
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 16.46129035949707
  num_agent_steps_sampled: 193400
  num_steps_sampled: 193400
  num_steps_trained: 193400
iterations_since_restore: 967
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf: {}
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.03763238044348938
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.05512157563147058
  mean_inference_ms: 0.720113814206088
  mean_raw_obs_processing_ms: 0.050793608338409985
time_since_restore: 178.13314700126648
time_this_iter_s

agent_timesteps_total: 195000
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-18
done: false
episode_len_mean: 199.66
episode_media: {}
episode_reward_max: 200.0
episode_reward_mean: 199.66
episode_reward_min: 181.0
episodes_this_iter: 1
episodes_total: 1184
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 17.286087036132812
  num_agent_steps_sampled: 195000
  num_steps_sampled: 195000
  num_steps_trained: 195000
iterations_since_restore: 975
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf: {}
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.0376260381362069
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.05511118463294772
  mean_inference_ms: 0.7199863233358808
  mean_raw_obs_processing_ms: 0.05078155983722192
time_since_restore: 179.50381112098694
time_this_iter

agent_timesteps_total: 196600
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-20
done: false
episode_len_mean: 200.0
episode_media: {}
episode_reward_max: 200.0
episode_reward_mean: 200.0
episode_reward_min: 200.0
episodes_this_iter: 1
episodes_total: 1192
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 18.51556396484375
  num_agent_steps_sampled: 196600
  num_steps_sampled: 196600
  num_steps_trained: 196600
iterations_since_restore: 983
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf: {}
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.03761653397419119
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.05509635806272567
  mean_inference_ms: 0.7197977519837673
  mean_raw_obs_processing_ms: 0.0507652013171635
time_since_restore: 180.68912482261658
time_this_iter_s:

agent_timesteps_total: 198200
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-21
done: false
episode_len_mean: 199.1
episode_media: {}
episode_reward_max: 200.0
episode_reward_mean: 199.1
episode_reward_min: 110.0
episodes_this_iter: 1
episodes_total: 1200
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 28.19048309326172
  num_agent_steps_sampled: 198200
  num_steps_sampled: 198200
  num_steps_trained: 198200
iterations_since_restore: 991
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 18.3
  gpu_util_percent0: 0.0
  ram_util_percent: 36.9
  vram_util_percent0: 0.05495228693649227
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.03760281129359328
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.055075454887749904
  mean_inference_ms: 0.7195266

agent_timesteps_total: 199800
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-22
done: false
episode_len_mean: 198.1
episode_media: {}
episode_reward_max: 200.0
episode_reward_mean: 198.1
episode_reward_min: 100.0
episodes_this_iter: 1
episodes_total: 1209
experiment_id: 9347da65e5334c0bba3d2e82feef9a20
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 19.154212951660156
  num_agent_steps_sampled: 199800
  num_steps_sampled: 199800
  num_steps_trained: 199800
iterations_since_restore: 999
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf: {}
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.03758641124230447
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.0550505983194443
  mean_inference_ms: 0.7191982758735478
  mean_raw_obs_processing_ms: 0.050717373889883975
time_since_restore: 183.06478834152222
time_this_iter_

In [13]:
print("Last checkpoint saved at", last_checkpoint)

Last checkpoint saved at /home/bruno/ray_results/PG_CartPole-v0_2021-11-16_17-41-58o964uy7w/checkpoint_001000/checkpoint-1000


Agora vamos criar outro vídeo, mas desta vez escolha a ação recomendada pelo modelo treinado em vez de agir aleatoriamente.

In [ ]:
trainer = pg.PGTrainer(config=config, env=environment_id)
trainer.restore(last_checkpoint)

after_training = os.path.join(
    DRIVE_PATH, "{}after_training_basic_api.mp4".format(environment_id)
)
after_video = VideoRecorder(env, after_training)
observation = env.reset()
done = False
while not done:
    env.render()
    after_video.capture_frame()
    action = trainer.compute_action(observation)
    observation, reward, done, info = env.step(action)
after_video.close()
env.close()
html = render_mp4(after_training)
HTML(html)

### Usando ambiente ou modelos personalizados

A API Python fornece a flexibilidade necessária para aplicar o RLlib a novos problemas. Você precisará usar esta API se desejar usar ambientes ou modelos personalizados com RLlib. Abaixo veremos um exemplo de um ambiente e um modelo customizado.

<br>


Para maiores informações veja em [APIs Python avançadas](https://docs.ray.io/en/latest/rllib-training.html#advanced-python-apis).

In [15]:
import gym
from gym.spaces import Discrete, Box
import numpy as np
import os
import random

import torch
import torch.nn as nn

import ray
from ray import tune
from ray.rllib.agents import pg
from ray.rllib.env.env_context import EnvContext
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.models.torch.fcnet import FullyConnectedNetwork as TorchFC
from ray.tune.logger import pretty_print

In [16]:
class SimpleCorridor(gym.Env):
    """Exemplo de um ambiente personalizado em que você tem que andar por um 
    corredor. Você pode configurar o comprimento do corredor através da 
    configuração do ambiente."""

    def __init__(self, config: EnvContext):
        self.end_pos = config["corridor_length"]
        self.cur_pos = 0
        self.action_space = Discrete(2)
        self.observation_space = Box(
            0.0, self.end_pos, shape=(1, ), dtype=np.float32)
        # Define a seed. É usado apenas para a recompensa final.
        self.seed(config.worker_index * config.num_workers)

    def reset(self):
        self.cur_pos = 0
        return [self.cur_pos]

    def step(self, action):
        assert action in [0, 1], action
        if action == 0 and self.cur_pos > 0:
            self.cur_pos -= 1
        elif action == 1:
            self.cur_pos += 1
        done = self.cur_pos >= self.end_pos
        # Produz uma recompensa aleatória quando atingirmos a meta.
        return [self.cur_pos], \
            random.random() * 2 if done else -0.1, done, {}

    def seed(self, seed=None):
        random.seed(seed)

In [17]:
class TorchCustomModel(TorchModelV2, nn.Module):
    """Exemplo de um modelo personalizado PyTorch que apenas delega para uma 
    fc-net."""

    def __init__(self, obs_space, action_space, num_outputs, model_config,
                 name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs,
                              model_config, name)
        nn.Module.__init__(self)

        self.torch_sub_model = TorchFC(obs_space, action_space, num_outputs,
                                       model_config, name)

    def forward(self, input_dict, state, seq_lens):
        input_dict["obs"] = input_dict["obs"].float()
        fc_out, _ = self.torch_sub_model(input_dict, state, seq_lens)
        return fc_out, []

    def value_function(self):
        return torch.reshape(self.torch_sub_model.value_function(), [-1])

In [18]:
# Também pode registrar a função de criar um ambiente explicitamente com:
# register_env("corridor", lambda config: SimpleCorridor(config))

# Registrar o modelo customizado
ModelCatalog.register_custom_model(
    "my_model", TorchCustomModel
)

config = {
    "env": SimpleCorridor,  # ou "corridor" se registrado
    "env_config": {
        "corridor_length": 5,
    },
    "model": {
        "custom_model": "my_model",
        "vf_share_layers": True,
    },
    "num_workers": 1,  
    "framework": "torch",
}

stop = {
    "training_iteration": 50,
    "timesteps_total": 100000,
    "episode_reward_mean": 0.1,
}

In [19]:
pg_config = pg.DEFAULT_CONFIG.copy()
pg_config.update(config)
pg_config["lr"] = 1e-3

trainer = pg.PGTrainer(config=pg_config, env=SimpleCorridor)
# executa o loop de treinamento manual e imprime os resultados após cada iteração
for _ in range(stop["training_iteration"]):
    result = trainer.train()
    print(pretty_print(result))
    
    # pare o treinamento caso tiver alcançado a quantidade de steps desejada
    # ou caso a recompensa desejada seja alcançada
    if result["timesteps_total"] >= stop["timesteps_total"] or \
            result["episode_reward_mean"] >= stop["episode_reward_mean"]:
        break

agent_timesteps_total: 200
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-32
done: false
episode_len_mean: 26.571428571428573
episode_media: {}
episode_reward_max: 1.3866340851152703
episode_reward_mean: -1.6236628243102207
episode_reward_min: -6.37245076204676
episodes_this_iter: 7
episodes_total: 7
experiment_id: f7f428ff01b14bbcbcd7382e4dbeff1e
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.6858269572257996
  num_agent_steps_sampled: 200
  num_steps_sampled: 200
  num_steps_trained: 200
iterations_since_restore: 1
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 18.5
  gpu_util_percent0: 0.0
  ram_util_percent: 38.5
  vram_util_percent0: 0.054129647910496875
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04035560645867343
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.02896963660

agent_timesteps_total: 1400
custom_metrics:
  default_policy: {}
date: 2021-11-16_17-45-33
done: false
episode_len_mean: 9.17
episode_media: {}
episode_reward_max: 1.5475504723193834
episode_reward_mean: 0.24254277682776265
episode_reward_min: -2.371372001398453
episodes_this_iter: 31
episodes_total: 123
experiment_id: f7f428ff01b14bbcbcd7382e4dbeff1e
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: 0.26876452565193176
  num_agent_steps_sampled: 1400
  num_steps_sampled: 1400
  num_steps_trained: 1400
iterations_since_restore: 7
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 18.5
  gpu_util_percent0: 0.0
  ram_util_percent: 36.9
  vram_util_percent0: 0.054129647910496875
pid: 6159
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.03909706424923176
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 0.02893375425175383

### Ray Tune

Todos os Trainers do RLlib são compatíveis com a API do [Ray Tune](https://docs.ray.io/en/master/tune/index.html). Isso permite que eles sejam facilmente usados em experimentos com o Tune. Por exemplo, o código a seguir executa o mesmo treino com o CartPole com o algoritmo PG.

In [20]:
import ray
config = {
    "env": environment_id,
    "framework": "torch",
}
stop = {"episode_reward_mean": 150, "timesteps_total": 100000}

# Executar o treinamento
analysis = ray.tune.run(
    "PG",
    config=config,
    stop=stop,
    checkpoint_freq=10,
    checkpoint_at_end=True,
    local_dir=os.path.join(DRIVE_PATH, "results")
)


(pid=12779) 2021-11-16 17:45:36,330	INFO trainer.py:696 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.


Result for PG_CartPole-v0_25270_00000:
  agent_timesteps_total: 200
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-45-36
  done: false
  episode_len_mean: 22.571428571428573
  episode_media: {}
  episode_reward_max: 38.0
  episode_reward_mean: 22.571428571428573
  episode_reward_min: 10.0
  episodes_this_iter: 7
  episodes_total: 7
  experiment_id: a3f8cb6e5c254863b66e662df36490ce
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 9.701666831970215
    num_agent_steps_sampled: 200
    num_steps_sampled: 200
    num_steps_trained: 200
  iterations_since_restore: 1
  node_ip: 192.168.0.102
  num_healthy_workers: 0
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 24.0
    gpu_util_percent0: 0.0
    ram_util_percent: 38.1
    vram_util_percent0: 0.054129647910496875
  pid: 12779
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing

Result for PG_CartPole-v0_25270_00000:
  agent_timesteps_total: 5800
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-45-41
  done: false
  episode_len_mean: 47.44
  episode_media: {}
  episode_reward_max: 164.0
  episode_reward_mean: 47.44
  episode_reward_min: 10.0
  episodes_this_iter: 1
  episodes_total: 142
  experiment_id: a3f8cb6e5c254863b66e662df36490ce
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 22.879854202270508
    num_agent_steps_sampled: 5800
    num_steps_sampled: 5800
    num_steps_trained: 5800
  iterations_since_restore: 29
  node_ip: 192.168.0.102
  num_healthy_workers: 0
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 18.7
    gpu_util_percent0: 0.0
    ram_util_percent: 38.2
    vram_util_percent0: 0.054294175715695954
  pid: 12779
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.0326227938

Result for PG_CartPole-v0_25270_00000:
  agent_timesteps_total: 12000
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-45-46
  done: false
  episode_len_mean: 97.02
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 97.02
  episode_reward_min: 13.0
  episodes_this_iter: 1
  episodes_total: 182
  experiment_id: a3f8cb6e5c254863b66e662df36490ce
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 17.509845733642578
    num_agent_steps_sampled: 12000
    num_steps_sampled: 12000
    num_steps_trained: 12000
  iterations_since_restore: 60
  node_ip: 192.168.0.102
  num_healthy_workers: 0
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 18.5
    gpu_util_percent0: 0.04
    ram_util_percent: 38.2
    vram_util_percent0: 0.054129647910496875
  pid: 12779
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.03389

Result for PG_CartPole-v0_25270_00000:
  agent_timesteps_total: 17200
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-45-51
  done: false
  episode_len_mean: 135.55
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 135.55
  episode_reward_min: 22.0
  episodes_this_iter: 1
  episodes_total: 212
  experiment_id: a3f8cb6e5c254863b66e662df36490ce
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 17.860557556152344
    num_agent_steps_sampled: 17200
    num_steps_sampled: 17200
    num_steps_trained: 17200
  iterations_since_restore: 86
  node_ip: 192.168.0.102
  num_healthy_workers: 0
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 18.1
    gpu_util_percent0: 0.31
    ram_util_percent: 38.1
    vram_util_percent0: 0.054129647910496875
  pid: 12779
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.034

2021-11-16 17:45:54,550	INFO tune.py:549 -- Total run time: 21.16 seconds (19.90 seconds for the tuning loop).


Embora o objeto de análise retornado do `ray.tune.run` anteriormente não tivesse nenhuma instância Trainer, ele tem todas as informações necessárias para reconstruir um de um checkpoint salvo.

O retorno do Ray Tune é um objeto [ExperimentAnalysis](https://docs.ray.io/en/latest/tune/api_docs/analysis.html?highlight=ExperimentAnalysis#experimentanalysis-tune-experimentanalysis) onde é possível resgatar qual o melhor checkpoint do treino.

In [21]:
from ray.rllib.agents.pg import PGTrainer

# restaurar um Trainer 
trial = analysis.get_best_logdir("episode_reward_mean", "max")
checkpoint = analysis.get_best_checkpoint(
    trial,
    "training_iteration",
    "max",
)
trainer = PGTrainer(config=config)
trainer.restore(checkpoint)

2021-11-16 17:45:55,270	INFO trainable.py:377 -- Restored on 192.168.0.102 from checkpoint: /home/bruno/Workspace/ceia-rl-curso/LAB_03/content/results/PG/PG_CartPole-v0_25270_00000_0_2021-11-16_17-45-34/checkpoint_000097/checkpoint-97
2021-11-16 17:45:55,271	INFO trainable.py:385 -- Current state after restoring: {'_iteration': 97, '_timesteps_total': None, '_time_total': 16.148224115371704, '_episodes_total': 223}


Agora vamos criar outro vídeo, mas desta vez escolha a ação recomendada pelo modelo treinado com a API Tune.

In [ ]:
after_training = after_training = os.path.join(
    DRIVE_PATH, "{}after_training_tune.mp4".format(environment_id)
)
after_video = VideoRecorder(env, after_training)
observation = env.reset()
done = False
while not done:
    env.render()
    after_video.capture_frame()
    action = trainer.compute_action(observation)
    observation, reward, done, info = env.step(action)
after_video.close()
env.close()
# You should get a video similar to the one below. 
html = render_mp4(after_training)
HTML(html)

O Tune gera arquivos do [Tensorboard](https://www.tensorflow.org/tensorboard) automaticamente durante o `tune.run()` Para visualizar a aprendizagem no tensorboard, execute o célula abaixo:

In [ ]:
if isColab:
    %tensorboard --logdir /content/gdrive/MyDrive/minicurso_rl/lab03/results/PG
else:
    %tensorboard --logdir ./content/results/PG

### Hyperparameter Tuning com o Ray Tune

[Ray Tune](https://docs.ray.io/en/latest/tune/index.html) é uma biblioteca para execução de experimentos e ajuste de hiperparâmetros. Vamos agora tentar encontrar hiperparâmetros que possam resolver o ambiente [Cartpole](https://gym.openai.com/envs/CartPole-v1/) no menor número de passos de tempo. Esteja preparado para que demore um pouco para ser executado.

In [24]:
parameter_search_config = {
    "env": environment_id,
    "framework": "torch",
    "num_gpus": 1,  # porcentagem da gpu disponível para treino
    "num_workers": 7,  # número de workers além do processo principal; no colab deve ser 1 pois só há 2 CPUs1
#     "num_envs_per_worker": 2,
    # Hyperparameter tuning
    "model": {
      "fcnet_hiddens": ray.tune.grid_search([[32], [64]]),
      "fcnet_activation": ray.tune.grid_search(["linear", "relu"]),
    },
    "lr": ray.tune.uniform(1e-7, 1e-2)
}

# To explicitly stop or restart Ray, use the shutdown API.
ray.shutdown()

ray.init(
    num_cpus=8,
    include_dashboard=False,
    ignore_reinit_error=True,
    log_to_driver=False,
)

parameter_search_analysis = ray.tune.run(
    "PG",
    config=parameter_search_config,
    stop=stop,
    num_samples=8,
    metric="timesteps_total",
    mode="min",
)

Result for PG_CartPole-v0_385d8_00000:
  agent_timesteps_total: 1400
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-46-38
  done: false
  episode_len_mean: 19.723076923076924
  episode_media: {}
  episode_reward_max: 69.0
  episode_reward_mean: 19.723076923076924
  episode_reward_min: 9.0
  episodes_this_iter: 65
  episodes_total: 65
  experiment_id: f512bb73236f46f0af80a3d19dab2175
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 8.085700988769531
    num_agent_steps_sampled: 1400
    num_steps_sampled: 1400
    num_steps_trained: 1400
  iterations_since_restore: 1
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 33.4
    gpu_util_percent0: 0.01
    ram_util_percent: 59.0
    vram_util_percent0: 0.16617308325106944
  pid: 13931
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_proce

Result for PG_CartPole-v0_385d8_00000:
  agent_timesteps_total: 21000
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-46-44
  done: false
  episode_len_mean: 46.02
  episode_media: {}
  episode_reward_max: 107.0
  episode_reward_mean: 46.02
  episode_reward_min: 15.0
  episodes_this_iter: 31
  episodes_total: 635
  experiment_id: f512bb73236f46f0af80a3d19dab2175
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 12.6880521774292
    num_agent_steps_sampled: 21000
    num_steps_sampled: 21000
    num_steps_trained: 21000
  iterations_since_restore: 15
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 90.5
    gpu_util_percent0: 0.12
    ram_util_percent: 59.2
    vram_util_percent0: 0.1686410003290556
  pid: 13931
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.07294202

Result for PG_CartPole-v0_385d8_00000:
  agent_timesteps_total: 40600
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-46-49
  done: false
  episode_len_mean: 54.33
  episode_media: {}
  episode_reward_max: 182.0
  episode_reward_mean: 54.33
  episode_reward_min: 19.0
  episodes_this_iter: 28
  episodes_total: 1022
  experiment_id: f512bb73236f46f0af80a3d19dab2175
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 12.191372871398926
    num_agent_steps_sampled: 40600
    num_steps_sampled: 40600
    num_steps_trained: 40600
  iterations_since_restore: 29
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 91.9
    gpu_util_percent0: 0.04
    ram_util_percent: 59.0
    vram_util_percent0: 0.1686410003290556
  pid: 13931
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.07305

Result for PG_CartPole-v0_385d8_00000:
  agent_timesteps_total: 60200
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-46-54
  done: false
  episode_len_mean: 69.32
  episode_media: {}
  episode_reward_max: 179.0
  episode_reward_mean: 69.32
  episode_reward_min: 23.0
  episodes_this_iter: 24
  episodes_total: 1335
  experiment_id: f512bb73236f46f0af80a3d19dab2175
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 13.868844985961914
    num_agent_steps_sampled: 60200
    num_steps_sampled: 60200
    num_steps_trained: 60200
  iterations_since_restore: 43
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf: {}
  pid: 13931
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.07373095336638234
    mean_env_render_ms: 0.0
    mean_env_wait_ms: 0.10520015107830613
    mean_inference_ms: 1.24159280882341

Result for PG_CartPole-v0_385d8_00000:
  agent_timesteps_total: 79800
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_17-46-59
  done: false
  episode_len_mean: 96.21
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 96.21
  episode_reward_min: 33.0
  episodes_this_iter: 10
  episodes_total: 1566
  experiment_id: f512bb73236f46f0af80a3d19dab2175
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 22.132614135742188
    num_agent_steps_sampled: 79800
    num_steps_sampled: 79800
    num_steps_trained: 79800
  iterations_since_restore: 57
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 88.9
    gpu_util_percent0: 0.04
    ram_util_percent: 59.2
    vram_util_percent0: 0.16929911154985192
  pid: 13931
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.0747

...

Result for PG_CartPole-v0_385d8_00030:
  agent_timesteps_total: 22400
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_18-01-47
  done: false
  episode_len_mean: 101.05
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 101.05
  episode_reward_min: 16.0
  episodes_this_iter: 7
  episodes_total: 397
  experiment_id: 5c2dcd48b905435a8b6a60115ec1f608
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 26.216829299926758
    num_agent_steps_sampled: 22400
    num_steps_sampled: 22400
    num_steps_trained: 22400
  iterations_since_restore: 16
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 83.6
    gpu_util_percent0: 0.01
    ram_util_percent: 65.1
    vram_util_percent0: 0.1771964461994077
  pid: 27947
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.07008

Result for PG_CartPole-v0_385d8_00030:
  agent_timesteps_total: 30800
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_18-01-50
  done: true
  episode_len_mean: 152.23
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 152.23
  episode_reward_min: 16.0
  episodes_this_iter: 7
  episodes_total: 445
  experiment_id: 5c2dcd48b905435a8b6a60115ec1f608
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 23.055614471435547
    num_agent_steps_sampled: 30800
    num_steps_sampled: 30800
    num_steps_trained: 30800
  iterations_since_restore: 22
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf: {}
  pid: 27947
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.07256182947180959
    mean_env_render_ms: 0.0
    mean_env_wait_ms: 0.10414332698032762
    mean_inference_ms: 1.230980384729126

Result for PG_CartPole-v0_385d8_00031:
  agent_timesteps_total: 21000
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_18-02-09
  done: false
  episode_len_mean: 83.94
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 83.94
  episode_reward_min: 24.0
  episodes_this_iter: 13
  episodes_total: 423
  experiment_id: 423f2a15e2654df485f11219f40daac0
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 18.95767593383789
    num_agent_steps_sampled: 21000
    num_steps_sampled: 21000
    num_steps_trained: 21000
  iterations_since_restore: 15
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 89.4
    gpu_util_percent0: 0.13
    ram_util_percent: 66.7
    vram_util_percent0: 0.18295491938137545
  pid: 28386
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.076005

Result for PG_CartPole-v0_385d8_00031:
  agent_timesteps_total: 39200
  custom_metrics:
    default_policy: {}
  date: 2021-11-16_18-02-14
  done: true
  episode_len_mean: 150.58
  episode_media: {}
  episode_reward_max: 200.0
  episode_reward_mean: 150.58
  episode_reward_min: 44.0
  episodes_this_iter: 8
  episodes_total: 550
  experiment_id: 423f2a15e2654df485f11219f40daac0
  hostname: bruno-odyssey-mint
  info:
    learner:
      default_policy:
        allreduce_latency: 0.0
        policy_loss: 24.39448356628418
    num_agent_steps_sampled: 39200
    num_steps_sampled: 39200
    num_steps_trained: 39200
  iterations_since_restore: 28
  node_ip: 192.168.0.102
  num_healthy_workers: 7
  off_policy_estimator: {}
  perf:
    cpu_util_percent: 83.9
    gpu_util_percent0: 0.05
    ram_util_percent: 66.3
    vram_util_percent0: 0.17851266864100032
  pid: 28386
  policy_reward_max: {}
  policy_reward_mean: {}
  policy_reward_min: {}
  sampler_perf:
    mean_action_processing_ms: 0.076527

2021-11-16 18:02:14,686	INFO tune.py:549 -- Total run time: 968.62 seconds (967.95 seconds for the tuning loop).


In [25]:
print(
    "Melhores hiperparâmetros encontrados:",
    parameter_search_analysis.best_config,
)

Melhores hiperparâmetros encontrados: {'env': 'CartPole-v0', 'framework': 'torch', 'num_gpus': 1, 'num_workers': 7, 'model': {'fcnet_hiddens': [64], 'fcnet_activation': 'linear'}, 'lr': 0.008777148144145926}


Especificando num_samples = 5 significa que você obterá cinco amostras aleatórias para a taxa de aprendizagem. Para cada um deles, existem dois valores para o tamanho da camada oculta e dois valores para a função de ativação. Portanto, haverá 5 * 2 * 2 = 20 tentativas, mostradas com seus status na saída da célula à medida que o cálculo é executado.

Observe que Ray mostra a melhor configuração atual à medida que avança. Isso inclui todos os valores padrão que foram definidos, o que é um bom lugar para encontrar outros parâmetros que podem ser ajustados.


# Exercício

Agora que você conhece a API básica do Ray Tune e da RLLib, **utilize o ambiente `BreakoutNoFrameskip-v4` e treine agentes com os algoritmos A3C, PPO e SAC**. Lembre-se de utilizar também o tensorboard para acompanhar e comparar as curvas de aprendizado de suas execuções.

Descrições dos algoritmos e seus respectivos hiperparâmetros podem ser encontrados [aqui](https://docs.ray.io/en/latest/rllib-algorithms.html#available-algorithms-overview).

#### 0. (Re)Imports + env

In [11]:
import gym
from gym.wrappers.monitoring.video_recorder import VideoRecorder
from gym.spaces import Discrete, Box

import ray
import ray.rllib.agents.pg as pg
from ray.tune.logger import pretty_print
from ray import tune
from ray.rllib.env.env_context import EnvContext
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.models.torch.fcnet import FullyConnectedNetwork as TorchFC
from ray.rllib.agents.pg import PGTrainer

from ray.rllib.models.preprocessors import get_preprocessor

import numpy as np
import os
import random

import torch
import torch.nn as nn

In [12]:
environment_id = "BreakoutNoFrameskip-v4"
env = gym.make(environment_id)

action_size = env.action_space.n
observation_size = env.observation_space.shape[0]
print(f"Action size: {action_size}\nObservation size: {observation_size}")

Action size: 4
Observation size: 210


In [13]:
def one_hot_encode(targets: np.ndarray, nb_classes: int):
    """Get one_hot_encode from integer action
    Thanks to: https://stackoverflow.com/a/42874726/5128626

    Args:
        targets (List[int]): Lista com inteiros
        nb_classes (int): número de classes

    Returns:
        List[List[float]]: Array of encoded targets
    """
    res = np.eye(nb_classes)[np.array(targets).reshape(-1)]
    return res.reshape(list(targets.shape)+[nb_classes])

In [14]:
ray.shutdown()
ray.init(ignore_reinit_error=True, include_dashboard=False)

{'node_ip_address': '192.168.0.102',
 'raylet_ip_address': '192.168.0.102',
 'redis_address': '192.168.0.102:6379',
 'object_store_address': '/tmp/ray/session_2021-11-17_21-29-14_906496_11466/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-11-17_21-29-14_906496_11466/sockets/raylet',
 'webui_url': None,
 'session_dir': '/tmp/ray/session_2021-11-17_21-29-14_906496_11466',
 'metrics_export_port': 62327,
 'node_id': 'e2243d24b8b161e3cae43f75ef1398bf95668ec16a34846348b7f9fd'}

#### 1. Visualizar agente aleatório

In [ ]:
# INSIRA AQUI O CÓDIGO PARA TREINAMENTO SOBRE O BreakoutNoFrameskip-v4
before_training = os.path.join(
    DRIVE_PATH, "{}_before_training.mp4".format(
        environment_id)
)
print(before_training)

video = VideoRecorder(env, before_training)
env.reset()
for i in range(200):
    env.render()
    video.capture_frame()
    # action = one_hot_encode(np.array([env.action_space.sample()]), action_size)
    observation, reward, done, info = env.step(env.action_space.sample())

video.close()
env.close()

html = render_mp4(before_training)
HTML(html)


#### 2. Treinar agente utilizando ray rllib

In [16]:
config = pg.DEFAULT_CONFIG.copy()
config["num_gpus"] = 0
config["num_workers"] = 1
config["lr"] = 0.0004
config["framework"] = "torch"


In [20]:
trainer = PGTrainer(config=config, env=environment_id)
episodes = 1000

for i in range(1, episodes+1):
    result = trainer.train()

    if i % 1 == 0:
        checkpoint = trainer.save()
        print(pretty_print(result))
        print("checkpoint saved at", checkpoint)

last_checkpoint = trainer.save()


2021-11-17 21:58:40,670	INFO trainable.py:101 -- Trainable.setup took 55.986 seconds. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.


agent_timesteps_total: 200
custom_metrics:
  default_policy: {}
date: 2021-11-17_21-58-41
done: false
episode_len_mean: 525.0
episode_media: {}
episode_reward_max: 0.0
episode_reward_mean: 0.0
episode_reward_min: 0.0
episodes_this_iter: 1
episodes_total: 1
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 200
  num_steps_sampled: 200
  num_steps_trained: 200
iterations_since_restore: 1
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 22.450000000000003
  gpu_util_percent0: 0.07
  ram_util_percent: 49.9
  vram_util_percent0: 0.059065482066469235
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04701709272849618
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.2608748763354856
  mean_inference_ms: 2.4366082243658416
  mean_raw_

agent_timesteps_total: 1400
custom_metrics:
  default_policy: {}
date: 2021-11-17_21-58-51
done: false
episode_len_mean: 652.1111111111111
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 1.0
episode_reward_min: 0.0
episodes_this_iter: 2
episodes_total: 9
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 1400
  num_steps_sampled: 1400
  num_steps_trained: 1400
iterations_since_restore: 7
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 30.15
  gpu_util_percent0: 0.02
  ram_util_percent: 50.2
  vram_util_percent0: 0.06638696939782823
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.050732477963325376
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.3985076727829207
  mean_inference_ms: 2.5705339794548503
  mean_r

agent_timesteps_total: 2600
custom_metrics:
  default_policy: {}
date: 2021-11-17_21-58-59
done: false
episode_len_mean: 658.2941176470588
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 1.0588235294117647
episode_reward_min: 0.0
episodes_this_iter: 2
episodes_total: 17
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 2600
  num_steps_sampled: 2600
  num_steps_trained: 2600
iterations_since_restore: 13
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 31.549999999999997
  gpu_util_percent0: 0.04
  ram_util_percent: 50.2
  vram_util_percent0: 0.06893715037841396
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.05100677222749256
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.417535837542987
  mean_inference_ms:

agent_timesteps_total: 3800
custom_metrics:
  default_policy: {}
date: 2021-11-17_21-59-07
done: false
episode_len_mean: 609.0
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 0.6428571428571429
episode_reward_min: 0.0
episodes_this_iter: 2
episodes_total: 28
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 3800
  num_steps_sampled: 3800
  num_steps_trained: 3800
iterations_since_restore: 19
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 41.2
  gpu_util_percent0: 0.03
  ram_util_percent: 51.25
  vram_util_percent0: 0.06646923330042777
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.05127401133112756
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.4317542203552567
  mean_inference_ms: 2.6116558642475107
  me

...

agent_timesteps_total: 194600
custom_metrics:
  default_policy: {}
date: 2021-11-17_22-19-11
done: false
episode_len_mean: 881.87
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 2.88
episode_reward_min: 0.0
episodes_this_iter: 1
episodes_total: 1043
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 194600
  num_steps_sampled: 194600
  num_steps_trained: 194600
iterations_since_restore: 973
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 62.5
  gpu_util_percent0: 0.0
  ram_util_percent: 52.8
  vram_util_percent0: 0.059230009871668314
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04949398333488615
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.3969825124101334
  mean_inference_ms: 2.5861893171367085
  mean_

agent_timesteps_total: 195800
custom_metrics:
  default_policy: {}
date: 2021-11-17_22-19-18
done: false
episode_len_mean: 881.91
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 2.88
episode_reward_min: 0.0
episodes_this_iter: 2
episodes_total: 1047
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 195800
  num_steps_sampled: 195800
  num_steps_trained: 195800
iterations_since_restore: 979
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 55.6
  gpu_util_percent0: 0.0
  ram_util_percent: 52.599999999999994
  vram_util_percent0: 0.059230009871668314
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04949002292754558
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.3969360184694866
  mean_inference_ms: 2.5859877479

agent_timesteps_total: 197000
custom_metrics:
  default_policy: {}
date: 2021-11-17_22-19-26
done: false
episode_len_mean: 859.53
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 2.7
episode_reward_min: 0.0
episodes_this_iter: 0
episodes_total: 1052
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 197000
  num_steps_sampled: 197000
  num_steps_trained: 197000
iterations_since_restore: 985
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 47.2
  gpu_util_percent0: 0.0
  ram_util_percent: 52.7
  vram_util_percent0: 0.059230009871668314
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04948472429398816
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.396865664275963
  mean_inference_ms: 2.5857383295078886
  mean_ra

agent_timesteps_total: 198200
custom_metrics:
  default_policy: {}
date: 2021-11-17_22-19-32
done: false
episode_len_mean: 848.25
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 2.61
episode_reward_min: 0.0
episodes_this_iter: 1
episodes_total: 1061
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 198200
  num_steps_sampled: 198200
  num_steps_trained: 198200
iterations_since_restore: 991
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 30.0
  gpu_util_percent0: 0.01
  ram_util_percent: 52.7
  vram_util_percent0: 0.059230009871668314
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04947106897790175
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.3965911760910041
  mean_inference_ms: 2.5850748961729204
  mean

agent_timesteps_total: 199400
custom_metrics:
  default_policy: {}
date: 2021-11-17_22-19-38
done: false
episode_len_mean: 836.68
episode_media: {}
episode_reward_max: 9.0
episode_reward_mean: 2.52
episode_reward_min: 0.0
episodes_this_iter: 1
episodes_total: 1068
experiment_id: 63e36b8ff9cc480c88a578ecff5b5385
hostname: bruno-odyssey-mint
info:
  learner:
    default_policy:
      allreduce_latency: 0.0
      policy_loss: -0.0
  num_agent_steps_sampled: 199400
  num_steps_sampled: 199400
  num_steps_trained: 199400
iterations_since_restore: 997
node_ip: 192.168.0.102
num_healthy_workers: 1
off_policy_estimator: {}
perf:
  cpu_util_percent: 50.0
  gpu_util_percent0: 0.0
  ram_util_percent: 52.7
  vram_util_percent0: 0.059230009871668314
pid: 11466
policy_reward_max: {}
policy_reward_mean: {}
policy_reward_min: {}
sampler_perf:
  mean_action_processing_ms: 0.04945899996746829
  mean_env_render_ms: 0.0
  mean_env_wait_ms: 1.3963026440425546
  mean_inference_ms: 2.5845018433189306
  mean_

In [21]:
print("Last checkpoint saved at", last_checkpoint)

Last checkpoint saved at /home/bruno/ray_results/PG_BreakoutNoFrameskip-v4_2021-11-17_21-57-444l1pd2dt/checkpoint_001000/checkpoint-1000


In [22]:
# See: https://docs.ray.io/en/releases-1.4.0/rllib-training.html
preprocessor = get_preprocessor(env.observation_space)(env.observation_space)

In [24]:
trainer = pg.PGTrainer(config=config, env=environment_id)
trainer.restore(last_checkpoint)

after_training = os.path.join(
    DRIVE_PATH, "{}after_training_basic_api.mp4".format(environment_id)
)
after_video = VideoRecorder(env, after_training)
observation = env.reset()
done = False
while not done:
    env.render()
    after_video.capture_frame()
    action = trainer.compute_action(preprocessor.transform(observation))
    observation, reward, done, info = env.step(action)
after_video.close()
env.close()


2021-11-18 01:03:07,824	INFO trainable.py:377 -- Restored on 192.168.0.102 from checkpoint: /home/bruno/ray_results/PG_BreakoutNoFrameskip-v4_2021-11-17_21-57-444l1pd2dt/checkpoint_001000/checkpoint-1000
2021-11-18 01:03:07,825	INFO trainable.py:385 -- Current state after restoring: {'_iteration': 1000, '_timesteps_total': None, '_time_total': 1215.3582525253296, '_episodes_total': 1071}


RuntimeError: Given groups=1, weight of size [16, 4, 8, 8], expected input[1, 3, 88, 88] to have 4 channels, but got 3 channels instead

In [ ]:
# Visualizar
html = render_mp4(after_training)
HTML(html)

#### 3. Treinar agente usando modelo pré-treinado

In [ ]:
class TorchCustomModel(TorchModelV2, nn.Module):
    """Exemplo de um modelo personalizado PyTorch que apenas delega para uma 
    fc-net."""

    def __init__(self, obs_space, action_space, num_outputs, model_config,
                 name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs,
                              model_config, name)
        nn.Module.__init__(self)

        self.torch_sub_model = TorchFC(obs_space, action_space, num_outputs,
                                       model_config, name)

    def forward(self, input_dict, state, seq_lens):
        input_dict["obs"] = input_dict["obs"].float()
        fc_out, _ = self.torch_sub_model(input_dict, state, seq_lens)
        return fc_out, []

    def value_function(self):
        return torch.reshape(self.torch_sub_model.value_function(), [-1])

In [ ]:
# Também pode registrar a função de criar um ambiente explicitamente com:
# register_env("corridor", lambda config: SimpleCorridor(config))

# Registrar o modelo customizado
ModelCatalog.register_custom_model(
    "my_model", TorchCustomModel
)

config = {
    "env": environment_id, 
    "env_config": {},
    "model": {
        "custom_model": "my_model",
        "vf_share_layers": True,
    },
    "num_workers": 1,  
    "framework": "torch",
}

stop = {
    "training_iteration": 1,  #50
    "timesteps_total": 100000,
    "episode_reward_mean": 0.1,
}


In [ ]:
pg_config = pg.DEFAULT_CONFIG.copy()
pg_config.update(config)
pg_config["lr"] = 1e-3

trainer = pg.PPOTrainer(config=pg_config, env=environment_id)
# executa o loop de treinamento manual e imprime os resultados após cada iteração
for _ in range(stop["training_iteration"]):
    result = trainer.train()
    print(pretty_print(result))
    
    # pare o treinamento caso tiver alcançado a quantidade de steps desejada
    # ou caso a recompensa desejada seja alcançada
    if result["timesteps_total"] >= stop["timesteps_total"] or \
            result["episode_reward_mean"] >= stop["episode_reward_mean"]:
        break


In [ ]:
after_training = os.path.join(
    DRIVE_PATH, "{}after_training_basic_api.mp4".format(environment_id)
)
after_video = VideoRecorder(env, after_training)
observation = env.reset()
done = False
while not done:
    env.render()
    after_video.capture_frame()
    action = trainer.compute_action(preprocessor.transform(observation))
    observation, reward, done, info = env.step(action)
after_video.close()
env.close()

#### 4. Ray Tune

In [ ]:
config = {
    "env": environment_id,
    "framework": "torch",
}
stop = {"timesteps_total": 10000}

# Executar o treinamento
analysis = ray.tune.run(
    "PPO",
    config=config,
    stop=stop,
    checkpoint_freq=100,
    checkpoint_at_end=True,
    local_dir=os.path.join(DRIVE_PATH, "results")
)


In [ ]:
# restaurar um Trainer 
trial = analysis.get_best_logdir("episode_reward_mean", "max")
checkpoint = analysis.get_best_checkpoint(
  trial,
  "training_iteration",
  "max",
)
trainer = PGTrainer(config=config)
trainer.restore(checkpoint)


In [ ]:
after_training = after_training = os.path.join(
    DRIVE_PATH, "{}after_training_tune.mp4".format(environment_id)
)
after_video = VideoRecorder(env, after_training)
observation = env.reset()
done = False
while not done:
    env.render()
    after_video.capture_frame()
    action = trainer.compute_action(preprocessor.transform(observation))
    observation, reward, done, info = env.step(action)
after_video.close()
env.close()
# You should get a video similar to the one below. 
html = render_mp4(after_training)
HTML(html)


In [ ]:
if isColab:
    %tensorboard --logdir /content/gdrive/MyDrive/minicurso_rl/lab03/results/PG
else:
    %tensorboard --logdir ./content/results/PG

#### 5. Hyperparameter Tune

In [ ]:
parameter_search_config = {
    "env": environment_id,
    "framework": "torch",
    "num_gpus": 1,  # porcentagem da gpu disponível para treino
    "num_workers": 1,  # número de workers além do processo principal; no colab deve ser 1 pois só há 2 CPUs

    # Hyperparameter tuning
    "model": {
      "fcnet_hiddens": ray.tune.grid_search([[32], [64]]),
      "fcnet_activation": ray.tune.grid_search(["linear", "relu"]),
    },
    "lr": ray.tune.uniform(1e-7, 1e-2)
}

# To explicitly stop or restart Ray, use the shutdown API.
ray.shutdown()

ray.init(
    num_cpus=2,
    include_dashboard=False,
    ignore_reinit_error=True,
    log_to_driver=False,
)

parameter_search_analysis = ray.tune.run(
    "PPO",
    config=parameter_search_config,
    stop=stop,
    num_samples=5,
    metric="timesteps_total",
    mode="min",
)

In [ ]:
print(
  "Melhores hiperparâmetros encontrados:",
  parameter_search_analysis.best_config,
)

# Bônus

Como tarefa bônus, experimente com os algoritmos aprendidos no ambiente `soccer_twos`, que será utilizado na competição final deste curso*. Para facilitar, utilize a variação `team_vs_policy` como no laboratório anterior.

<img src="https://raw.githubusercontent.com/bryanoliveira/soccer-twos-env/master/images/screenshot.png" height="400">

> Visualização do ambiente

Este ambiente consiste em um jogo de futebol de carros 2x2, ou seja, o objetivo é marcar um gol no adversário o mais rápido possível. Na variação `team_vs_policy`, seu agente controla um jogador do time azul e joga contra um time aleatório. Mais informações sobre o ambiente podem ser encontradas [no repositório](https://github.com/bryanoliveira/soccer-twos-env) e [na documentação do Unity ml-agents](https://github.com/Unity-Technologies/ml-agents/blob/main/docs/Learning-Environment-Examples.md#soccer-twos).


**Sua tarefa é treinar um agente com a interface do Ray apresentada, experimentando com diferentes algoritmos e hiperparâmetros.**


<br>

*A variação utilizada na competição será a `multiagent_player`, mas agentes treinados para `team_vs_policy` podem ser facilmente adaptados. Na seção "Exportando seu agente treinado" o agente "MyDqnSoccerAgent" faz exatamente isso.

Utilize o ambiente instanciado abaixo para executar o algoritmo de treinamento. Ao final da execução, a recompensa do seu agente por episódio deve tender a +2.

In [14]:
import gym
from gym.wrappers.monitoring.video_recorder import VideoRecorder
from gym.spaces import Discrete, Box

import ray
import ray.rllib.agents.ppo as pg
from ray.tune.logger import pretty_print
from ray import tune
from ray.rllib.env.env_context import EnvContext
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.models.torch.fcnet import FullyConnectedNetwork as TorchFC
from ray.rllib.agents.ppo import PPOTrainer

import numpy as np
import os
import random

import torch
import torch.nn as nn

In [15]:
import soccer_twos

# Fecha o ambiente caso tenha sido aberto anteriormente
try: env.close()
except: pass

env = soccer_twos.make(
    variation=soccer_twos.EnvType.team_vs_policy,
    flatten_branched=True, # converte o action_space de MultiDiscrete para Discrete
    single_player=True, # controla um dos jogadores enquanto os outros ficam parados
    opponent_policy=lambda *_: 0,  # faz os oponentes ficarem parados
)

environment_id = "soccer-v0"

# Obtem tamanhos de estado e ação
state_size = env.observation_space.shape[0]
action_size = env.action_space.n

print("Tamanho do estado: {}, tamanho da ação: {}".format(state_size, action_size))
env.close()

[INFO] Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0


INFO:mlagents_envs.environment:Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0


[INFO] Connected new brain: SoccerTwos?team=1


INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=1


[INFO] Connected new brain: SoccerTwos?team=0


INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=0


Tamanho do estado: 336, tamanho da ação: 27


In [24]:
ray.shutdown()
ray.init(num_cpus=4, ignore_reinit_error=True, include_dashboard=False)

{'node_ip_address': '192.168.0.102',
 'raylet_ip_address': '192.168.0.102',
 'redis_address': '192.168.0.102:12844',
 'object_store_address': '/tmp/ray/session_2021-11-18_15-03-27_313316_269868/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-11-18_15-03-27_313316_269868/sockets/raylet',
 'webui_url': None,
 'session_dir': '/tmp/ray/session_2021-11-18_15-03-27_313316_269868',
 'metrics_export_port': 61492,
 'node_id': '1a6b1fec0972210a0e500c5656b6e833cea2e29e62c329b0e949d334'}

In [25]:
def create_rllib_env(env_config: dict = {}):
    # suporte a múltiplas instâncias do ambiente na mesma máquina
    if hasattr(env_config, "worker_index"):
        env_config["worker_id"] = (
            env_config.worker_index * env_config.get("num_envs_per_worker", 1)
            + env_config.vector_index
        )
    return soccer_twos.make(**env_config)

# registra ambiente no Ray
tune.registry.register_env(environment_id, create_rllib_env)

In [26]:
NUM_ENVS_PER_WORKER = 1

Utilize a configuração abaixo como ponto de partida para seus testes. 

A parte mais imporante é a chave `env_config`, que configura o ambiente para ser compatível com o agente disponibilizado para exportação do seu agente. Neste ponto do curso você já deve conseguir testar as outras variações do ambiente e utilizar as APIs do Ray para treinar um agente próximo (ou melhor) do que o [ceia_baseline_agent](https://drive.google.com/file/d/1WEjr48D7QG9uVy1tf4GJAZTpimHtINzE/view). Exemplos de como utilizar as outras variações podem ser encontrados [aqui](https://github.com/dlb-rl/rl-tournament-starter/). Ao utilizar essas variações, você deve utilizar também outras definições de agente para lidar com os diferentes espaços de observação e ação (que também estão presentes nos exemplos).

In [27]:
analysis = tune.run(
    "PPO",
    num_samples=1,
    config={
        # system settings
        "num_gpus": 1,
        "num_workers": 3,
#         "num_envs_per_worker": NUM_ENVS_PER_WORKER,
        "log_level": "INFO",
        "framework": "torch",
        # RL setup
        "env": environment_id,
        "env_config": {
            "variation": soccer_twos.EnvType.team_vs_policy,
            "single_player": True,
            "flatten_branched": True,
            "opponent_policy": lambda *_: 0,
        },
    },
    stop={
        # 10000000 (10M) de steps podem ser necessários para aprender uma política útil
        "timesteps_total": int(15e6),
        # você também pode limitar por tempo, de acordo com o tempo limite do colab
#         "time_total_s": 14400, # 4h
        "time_total_s": 86400, # 24h
    },
    checkpoint_freq=100,
    checkpoint_at_end=True,
    local_dir=os.path.join(DRIVE_PATH, "results"),
)

(pid=324759) 2021-11-18 15:03:33,183	WARNING ppo.py:135 -- `train_batch_size` (4000) cannot be achieved with your other settings (num_workers=3 num_envs_per_worker=1 rollout_fragment_length=200)! Auto-adjusting `rollout_fragment_length` to 1333.


(pid=324757) [INFO] Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0
(pid=324757) [INFO] Connected new brain: SoccerTwos?team=1
(pid=324757) [INFO] Connected new brain: SoccerTwos?team=0


(pid=324757) INFO:mlagents_envs.environment:Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0
(pid=324757) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=1
(pid=324757) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=0
(pid=324757) 2021-11-18 15:03:38,180	INFO torch_policy.py:134 -- TorchPolicy (worker=1) running on CPU.
(pid=324756) INFO:mlagents_envs.environment:Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0
(pid=324756) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=1
(pid=324756) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=0


(pid=324756) [INFO] Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0
(pid=324756) [INFO] Connected new brain: SoccerTwos?team=1
(pid=324756) [INFO] Connected new brain: SoccerTwos?team=0


(pid=324759) 2021-11-18 15:03:38,360	INFO torch_policy.py:148 -- TorchPolicy (worker=local) running on 1 GPU(s).
(pid=324756) 2021-11-18 15:03:38,405	INFO torch_policy.py:134 -- TorchPolicy (worker=3) running on CPU.
(pid=324758) INFO:mlagents_envs.environment:Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0


(pid=324758) [INFO] Connected to Unity environment with package version 2.1.0-exp.1 and communication version 1.5.0
(pid=324758) [INFO] Connected new brain: SoccerTwos?team=1
(pid=324758) [INFO] Connected new brain: SoccerTwos?team=0


(pid=324758) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=1
(pid=324758) INFO:mlagents_envs.environment:Connected new brain: SoccerTwos?team=0
(pid=324758) 2021-11-18 15:03:38,732	INFO torch_policy.py:134 -- TorchPolicy (worker=2) running on CPU.
(pid=324759) 2021-11-18 15:03:40,815	INFO rollout_worker.py:1199 -- Built policy map: {'default_policy': <ray.rllib.policy.policy_template.PPOTorchPolicy object at 0x7fd4e022a6d0>}
(pid=324759) 2021-11-18 15:03:40,815	INFO rollout_worker.py:1200 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7fd4e022a520>}
(pid=324759) 2021-11-18 15:03:40,815	INFO rollout_worker.py:583 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7fd4e0204730>}
2021-11-18 15:03:40,904	ERROR trial_runner.py:748 -- Trial PPO_soccer-v0_d6059_00000: Error processing event.
Traceback (most recent call last):
  File "/home/bruno/anaconda3/envs/soccer-twos/lib/pyth

Result for PPO_soccer-v0_d6059_00000:
  {}
  


(pid=324759) 2021-11-18 15:03:40,899	INFO trainer.py:601 -- Worker crashed during call to train(). To attempt to continue training without the failed worker, set `'ignore_worker_failures': True`.
(pid=324757) 2021-11-18 15:03:40,889	INFO rollout_worker.py:723 -- Generating sample batch of size 1333
(pid=324756) 2021-11-18 15:03:42,001	ERROR worker.py:409 -- SystemExit was raised from the worker
(pid=324756) Traceback (most recent call last):
(pid=324756)   File "python/ray/_raylet.pyx", line 490, in ray._raylet.execute_task
(pid=324756)   File "python/ray/_raylet.pyx", line 497, in ray._raylet.execute_task
(pid=324756)   File "python/ray/_raylet.pyx", line 501, in ray._raylet.execute_task
(pid=324756)   File "python/ray/_raylet.pyx", line 451, in ray._raylet.execute_task.function_executor
(pid=324756)   File "/home/bruno/anaconda3/envs/soccer-twos/lib/python3.8/site-packages/ray/_private/function_manager.py", line 563, in actor_method_executor
(pid=324756)     return method(__ray_actor

TuneError: ('Trials did not complete', [PPO_soccer-v0_d6059_00000])

## Exportando seu agente treinado

Assim como no Lab 02, você pode exportar seu agente treinado para ser executado como competidor no ambiente da competição ou simplesmente assistí-lo. Para isso, devemos definir uma classe de agente que implemente a interface e trate as observações/ações para o formato da competição. Abaixo, configuramos qual experimento/checkpoint exportar e guardamos a implementação em uma variável para salvá-la em um arquivo posteriormente.

In [98]:
ALGORITHM = "PPO"
TRIAL = analysis.get_best_logdir("episode_reward_mean", "max")
CHECKPOINT = analysis.get_best_checkpoint(
  TRIAL,
  "training_iteration",
  "max",
)
TRIAL, CHECKPOINT

('/home/bruno/Workspace/ceia-rl-curso/LAB_03/content/results/PPO/PPO_soccer-v0_3fbc3_00000_0_lr=9.7555e-05_2021-11-15_17-54-39',
 '/home/bruno/Workspace/ceia-rl-curso/LAB_03/content/results/PPO/PPO_soccer-v0_3fbc3_00000_0_lr=9.7555e-05_2021-11-15_17-54-39/checkpoint_001252/checkpoint-1252')

In [99]:
agent_file = f"""
import pickle
import os

import gym
from gym_unity.envs import ActionFlattener
import ray
from ray import tune
from ray.tune.registry import get_trainable_cls

from soccer_twos import AgentInterface, DummyEnv


ALGORITHM = "{ALGORITHM}"
CHECKPOINT_PATH = os.path.join(
    os.path.dirname(os.path.abspath(__file__)), 
    "{CHECKPOINT.split("LAB_03/")[1]}"
)


class MyRaySoccerAgent(AgentInterface):
    def __init__(self, env: gym.Env):
        super().__init__()
        ray.init(ignore_reinit_error=True)

        self.flattener = ActionFlattener(env.action_space.nvec)

        # Load configuration from checkpoint file.
        config_path = ""
        if CHECKPOINT_PATH:
            config_dir = os.path.dirname(CHECKPOINT_PATH)
            config_path = os.path.join(config_dir, "params.pkl")
            # Try parent directory.
            if not os.path.exists(config_path):
                config_path = os.path.join(config_dir, "../params.pkl")

        # Load the config from pickled.
        if os.path.exists(config_path):
            with open(config_path, "rb") as f:
                config = pickle.load(f)
        else:
            # If no config in given checkpoint -> Error.
            raise ValueError(
                "Could not find params.pkl in either the checkpoint dir or "
                "its parent directory!"
            )

        # no need for parallelism on evaluation
        config["num_workers"] = 0
        config["num_gpus"] = 0

        # create a dummy env since it's required but we only care about the policy
        obs_space = env.observation_space
        act_space = self.flattener.action_space
        tune.registry.register_env(
            "DummyEnv",
            lambda *_: DummyEnv(obs_space, act_space),
        )
        config["env"] = "DummyEnv"

        # create the Trainer from config
        cls = get_trainable_cls(ALGORITHM)
        agent = cls(env=config["env"], config=config)
        # load state from checkpoint
        agent.restore(CHECKPOINT_PATH)
        # get default policy for evaluation
        self.policy = agent.get_policy()

    def act(self, observation):
        actions = {{}}
        for player_id in observation:
            # compute_single_action returns a tuple of (action, action_info, ...)
            # as we only need the action, we discard the other elements
            actions[player_id] = self.flattener.lookup_action(
                self.policy.compute_single_action(observation[player_id])[0]
            )
        return actions
"""

In [100]:
import os
import shutil

agent_name = "my_ray_soccer_agent"
agent_path = os.path.join(
    DRIVE_PATH, agent_name, agent_name) if isColab else os.path.join(DRIVE_PATH, agent_name)
os.makedirs(agent_path, exist_ok=True)

shutil.rmtree(agent_path)
os.makedirs(agent_path)

# salva a classe do agente
with open(os.path.join(agent_path, "agent.py"), "w") as f:
    f.write(agent_file)

# salva um __init__ para criar o módulo Python
with open(os.path.join(agent_path, "__init__.py"), "w") as f:
    f.write("from .agent import MyRaySoccerAgent")

# copia o trial inteiro, incluindo os arquivos de configuração do experimento
shutil.copytree(TRIAL, os.path.join(agent_path, TRIAL.split("LAB_03/")[1]))

# empacota tudo num arquivo .zip
if isColab:
    shutil.make_archive(os.path.join(DRIVE_PATH, agent_name),
                        "zip", os.path.join(DRIVE_PATH, agent_name))


Após empacotar todos os arquivos necessários para a execução do seu agente, será criado um arquivo `minicurso_rl/lab03/my_ray_soccer_agent.zip` nos arquivos do Colab e na pasta correspondente no Google Drive. Baixe o arquivo e extraia-o para alguma pasta no seu computador. 

Assumindo que o ambiente Python já está configurado (e.g. os pacotes no [requirements.txt](https://github.com/dlb-rl/rl-tournament-starter/blob/main/requirements.txt) estão instalados), rode `python -m soccer_twos.watch -m my_ray_soccer_agent` para assistir seu agente jogando contra si mesmo. 

Você também pode testar dois agentes diferentes jogando um contra o outro. Utilize o seguinte comando: `python -m soccer_twos.watch -m1 my_ray_soccer_agent -m2 ceia_baseline_agent`. Você pode baixar o agente *ceia_baseline_agent* [aqui](https://drive.google.com/file/d/1WEjr48D7QG9uVy1tf4GJAZTpimHtINzE/view).